In [0]:
from pyspark.sql.types import * 
from pyspark.sql.functions import split
df = spark.read.csv("/FileStore/tables/Australian_Vehicle_Prices.csv", inferSchema=True, header=True)
df.show(5)

+-------------+----+------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-----------------+-----------------+---------+--------+--------+------+
|        Brand|Year| Model|             Car/Suv|               Title|UsedOrNew|Transmission|      Engine|DriveType|FuelType|FuelConsumption|Kilometres| ColourExtInt|         Location|CylindersinEngine| BodyType|   Doors|   Seats| Price|
+-------------+----+------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-----------------+-----------------+---------+--------+--------+------+
|    Ssangyong|2022|Rexton|Sutherland Isuzu Ute|2022 Ssangyong Re...|     DEMO|   Automatic|4 cyl, 2.2 L|      AWD|  Diesel| 8.7 L / 100 km|      5595|White / Black|   Caringbah, NSW|            4 cyl|      SUV| 4 Doors| 7 Seats| 51990|
|           MG|2022|   MG3|           Hatchback|2022

In [0]:
df.printSchema()

root
 |-- Brand: string (nullable = true)
 |-- Year: string (nullable = true)
 |-- Model: string (nullable = true)
 |-- Car/Suv: string (nullable = true)
 |-- Title: string (nullable = true)
 |-- UsedOrNew: string (nullable = true)
 |-- Transmission: string (nullable = true)
 |-- Engine: string (nullable = true)
 |-- DriveType: string (nullable = true)
 |-- FuelType: string (nullable = true)
 |-- FuelConsumption: string (nullable = true)
 |-- Kilometres: string (nullable = true)
 |-- ColourExtInt: string (nullable = true)
 |-- Location: string (nullable = true)
 |-- CylindersinEngine: string (nullable = true)
 |-- BodyType: string (nullable = true)
 |-- Doors: string (nullable = true)
 |-- Seats: string (nullable = true)
 |-- Price: string (nullable = true)



In [0]:
split_engine = split(df['Engine'], ', ')
df = df.withColumn('EngineCapacity', regexp_extract(split_engine.getItem(1), r"(\d+\.\d+)", 0).cast("double"))
df = df.withColumn('Seats', regexp_extract("Seats", r"(\d+\.\d+)", 0).cast("double") )
df = df.withColumn('Doors', regexp_extract("Doors", r"(\d+\.\d+)", 0).cast("double") )



df.show(5)


+-------------+----+------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-----------------+-----------------+---------+-----+-----+------+--------------+-----------+
|        Brand|Year| Model|             Car/Suv|               Title|UsedOrNew|Transmission|      Engine|DriveType|FuelType|FuelConsumption|Kilometres| ColourExtInt|         Location|CylindersinEngine| BodyType|Doors|Seats| Price|EngineCapacity|Consumption|
+-------------+----+------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-----------------+-----------------+---------+-----+-----+------+--------------+-----------+
|    Ssangyong|2022|Rexton|Sutherland Isuzu Ute|2022 Ssangyong Re...|     DEMO|   Automatic|4 cyl, 2.2 L|      AWD|  Diesel| 8.7 L / 100 km|      5595|White / Black|   Caringbah, NSW|            4 cyl|      SUV| null| null| 51

In [0]:
from pyspark.sql.functions import regexp_extract, round, isnan, count
df = df.withColumn("Consumption", round(100 / regexp_extract("FuelConsumption", r"(\d+\.\d+)", 0).cast("double"), 2))
df.show()


+-------------+----+---------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-------------------+-----------------+----------+--------+--------+------+--------------+-----------+
|        Brand|Year|    Model|             Car/Suv|               Title|UsedOrNew|Transmission|      Engine|DriveType|FuelType|FuelConsumption|Kilometres| ColourExtInt|           Location|CylindersinEngine|  BodyType|   Doors|   Seats| Price|EngineCapacity|Consumption|
+-------------+----+---------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-------------------+-----------------+----------+--------+--------+------+--------------+-----------+
|    Ssangyong|2022|   Rexton|Sutherland Isuzu Ute|2022 Ssangyong Re...|     DEMO|   Automatic|4 cyl, 2.2 L|      AWD|  Diesel| 8.7 L / 100 km|      5595|White / Black|     Caringbah, NSW|  

In [0]:
from pyspark.sql.functions import when, count, col, sequence
df.where(df.Price.isNull()).count()
df.select([count(when(col(c).isNull(), c)).alias(c) for c in df.columns]).show() 

+-----+----+-----+-------+-----+---------+------------+------+---------+--------+---------------+----------+------------+--------+-----------------+--------+-----+-----+-----+--------------+-----------+
|Brand|Year|Model|Car/Suv|Title|UsedOrNew|Transmission|Engine|DriveType|FuelType|FuelConsumption|Kilometres|ColourExtInt|Location|CylindersinEngine|BodyType|Doors|Seats|Price|EngineCapacity|Consumption|
+-----+----+-----+-------+-----+---------+------------+------+---------+--------+---------------+----------+------------+--------+-----------------+--------+-----+-----+-----+--------------+-----------+
|    1|   0|    1|     55|  183|      182|          92|   183|      183|     183|            183|       183|         183|     632|              182|     409| 1695| 1796|  185|          1874|       3772|
+-----+----+-----+-------+-----+---------+------------+------+---------+--------+---------------+----------+------------+--------+-----------------+--------+-----+-----+-----+-------------

In [0]:
df = df.dropna(subset=["Price"])
df.show()

+-------------+----+---------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-------------------+-----------------+----------+--------+--------+------+
|        Brand|Year|    Model|             Car/Suv|               Title|UsedOrNew|Transmission|      Engine|DriveType|FuelType|FuelConsumption|Kilometres| ColourExtInt|           Location|CylindersinEngine|  BodyType|   Doors|   Seats| Price|
+-------------+----+---------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-------------------+-----------------+----------+--------+--------+------+
|    Ssangyong|2022|   Rexton|Sutherland Isuzu Ute|2022 Ssangyong Re...|     DEMO|   Automatic|4 cyl, 2.2 L|      AWD|  Diesel| 8.7 L / 100 km|      5595|White / Black|     Caringbah, NSW|            4 cyl|       SUV| 4 Doors| 7 Seats| 51990|
|           MG|2022|      MG

In [0]:
from pyspark.ml.feature import Bucketizer
from pyspark.sql.functions import col
df = df.withColumn("Kilometres", col("Kilometres").cast(DoubleType()))


splits = [-float("inf"), 20000, 40000, 60000, 80000, float("inf")]
bucketizer = Bucketizer(splits=splits, inputCol="Kilometres", outputCol="KilometresCategory")
df = bucketizer.transform(df)
df.show()

+-------------+----+---------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-------------------+-----------------+----------+-----+-----+------+--------------+-----------+------------------+
|        Brand|Year|    Model|             Car/Suv|               Title|UsedOrNew|Transmission|      Engine|DriveType|FuelType|FuelConsumption|Kilometres| ColourExtInt|           Location|CylindersinEngine|  BodyType|Doors|Seats| Price|EngineCapacity|Consumption|KilometresCategory|
+-------------+----+---------+--------------------+--------------------+---------+------------+------------+---------+--------+---------------+----------+-------------+-------------------+-----------------+----------+-----+-----+------+--------------+-----------+------------------+
|    Ssangyong|2022|   Rexton|Sutherland Isuzu Ute|2022 Ssangyong Re...|     DEMO|   Automatic|4 cyl, 2.2 L|      AWD|  Diesel| 8.7 L / 100 km|    5595

In [0]:
display(df)

Brand Year Model Car/Suv Title UsedOrNew Transmission Engine DriveType FuelType FuelConsumption Kilometres ColourExtInt Location CylindersinEngine BodyType Doors Seats Price EngineCapacity Consumption KilometresCategory Ssangyong 2022 Rexton Sutherland Isuzu Ute 2022 Ssangyong Rexton Ultimate (awd) DEMO Automatic 4 cyl, 2.2 L AWD Diesel 8.7 L / 100 km 5595.0 White / Black Caringbah, NSW 4 cyl SUV null null 51990 2.2 11.49 0.0 MG 2022 MG3 Hatchback 2022 MG MG3 Auto Excite (with Navigation) USED Automatic 4 cyl, 1.5 L Front Premium 6.7 L / 100 km 16.0 Black / Black Brookvale, NSW 4 cyl Hatchback null null 19990 1.5 14.93 0.0 BMW 2022 430I Coupe 2022 BMW 430I M Sport USED Automatic 4 cyl, 2 L Rear Premium 6.6 L / 100 km 8472.0 Grey / White Sylvania, NSW 4 cyl Coupe null null 108988 null 15.15 0.0 Mercedes-Benz 2011 E500 Coupe 2011 Mercedes-Benz E500 Elegance USED Automatic 8 cyl, 5.5 L Rear Premium 11 L / 100 km 136517.0 White / Brown Mount Druitt, NSW 8 cyl Coupe null null 32990 5.5 null 4.0 Renault 2022 Arkana SUV 2022 Renault Arkana Intens USED Automatic 4 cyl, 1.3 L Front Unleaded 6 L / 100 km 1035.0 Grey / Black Castle Hill, NSW 4 cyl SUV null null 34990 1.3 null 0.0 Toyota 2004 Estima ON FOUR WHEELS 2004 Toyota Estima T EDITION USED Automatic - Other Unleaded - 160230.0 Grey / - Saint Marys, NSW - Commercial null null 9990 null null 4.0 Land 2017 Rover SUV 2017 Land Rover Range Rover Evoque TD4 180 HSE Dynamic USED Automatic 4 cyl, 2 L AWD Diesel 5.1 L / 100 km 67662.0 White / Black Blacktown, NSW 4 cyl SUV null null 62280 null 19.61 3.0 Nissan 2000 Pulsar Hatchback 2000 Nissan Pulsar LX USED Automatic 4 cyl, 1.6 L Front Unleaded 8 L / 100 km 300539.0 Red / Grey Wentworthville, NSW 4 cyl Hatchback null null 2995 1.6 null 4.0 Toyota 2013 86 Coupe 2013 Toyota 86 GT USED Automatic 4 cyl, 2 L Rear Premium 7.1 L / 100 km 82012.0 Black / - Mcgraths Hill, NSW 4 cyl Coupe null null 24888 null 14.08 4.0 Honda 2014 Jazz Hatchback 2014 Honda Jazz Hybrid USED Automatic 4 cyl, 1.3 L Front Hybrid 4.5 L / 100 km 38229.0 Blue / - Lidcombe, NSW 4 cyl Hatchback null null 17900 1.3 22.22 1.0 Toyota 2009 HiAce Carbarn 2009 Toyota HiAce (No Badge) USED Automatic - Other Unleaded - 148190.0 White / - Lidcombe, NSW - Commercial null null 42500 null null 4.0 Toyota 2018 HiAce Commercial 2018 Toyota HiAce LWB USED Automatic 4 cyl, 2.7 L Rear Unleaded 9.8 L / 100 km 16324.0 White / Grey Lidcombe, NSW 4 cyl Commercial null null 41999 2.7 10.2 0.0 Honda 2015 City USED Dealer ad 2015 Honda City GM VTi-L Sedan 4dr CVT 7sp 1.5i MY16 USED Automatic - Other Unleaded - 181745.0 Black / - Rouse Hill, NSW - null null null 11999 null null 4.0 Toyota 2017 HiAce USED Dealer ad 2017 Toyota HiAce USED Automatic - Other - - 136296.0 Silver / Grey Lidcombe, NSW - null null null 38999 null null 4.0 Toyota 2016 HiAce Commercial 2016 Toyota HiAce LWB USED Automatic 4 cyl, 3 L Rear Diesel 8 L / 100 km 229829.0 White / Grey Lidcombe, NSW 4 cyl Commercial null null 27995 null null 4.0 Volkswagen 2012 Golf Hatchback 2012 Volkswagen Golf 90 TSI Trendline USED Automatic 4 cyl, 1.4 L Front Premium 6.2 L / 100 km 55676.0 White / Black Five Dock, NSW 4 cyl Hatchback null null 14999 1.4 16.13 2.0 BMW 2014 X3 SUV 2014 BMW X3 Xdrive 20D USED Automatic 4 cyl, 2 L 4WD Diesel 5.6 L / 100 km 82624.0 Black / Black Haberfield, NSW 4 cyl SUV null null 24985 null 17.86 4.0 Mitsubishi 2013 Outlander Exclusive Autohaus 2013 Mitsubishi Outlander ES USED Manual - Other - - 120020.0 Blue / Grey Blacktown, NSW - Wagon null null 13999 null null 4.0 BMW 2011 118D Hatchback 2011 BMW 118D USED Automatic 4 cyl, 2 L Rear Diesel 5.4 L / 100 km 95204.0 Silver / - Five Dock, NSW 4 cyl Hatchback null null 13999 null 18.52 4.0 Ford 2014 Fiesta Hatchback 2014 Ford Fiesta Sport USED Automatic 3 cyl, 1 L Front Unleaded 5.4 L / 100 km 76289.0 White / Black Cabramatta, NSW 3 cyl Hatchback null null 12400 null 18.52 3.0 Mitsubishi 2012 Outlander SUV 2012 Mitsubishi Outlander LS (4X4) USED Automatic 4 cyl, 2.4 L

## Análise de Tendências de Preços

### Variação de preço em relação ao ano do veículo

In [0]:
from pyspark.sql.functions import sum, avg
price_year = df.groupBy("Year", "UsedOrNew").agg(avg("Price").alias("AveragePrice"))
display(price_year)

Year UsedOrNew AveragePrice 1991 USED 29800.0 2004 USED 13960.726495726496 1995 USED 44937.5 2005 USED 14661.96511627907 2000 NEW 63990.0 2011 NEW 16999.0 2021 DEMO 90708.33333333333 2002 USED 20351.666666666668 2013 USED 20672.59430604982 1979 USED 29888.0 1970 USED 129990.0 1940 USED 64990.0 2003 USED 14828.918918918918 2012 USED 19656.030172413793 1996 USED 19968.625 1978 USED 97500.0 2001 USED 17335.64864864865 1986 USED 69990.0 1993 USED 42043.0 2015 USED 28272.248843663274 2022 NEW 51102.92452830189 1981 USED 19545.0 2022 DEMO 62019.3322147651 1985 USED 59495.0 2016 USED 32462.727921498663 1990 USED 59751.8 2023 USED 78965.7094972067 1997 USED 22228.222222222223 2007 USED 16790.578358208953 2020 USED 45324.94792586055 2000 USED 14321.75 1989 USED 39573.2 2021 NEW 27990.0 2019 USED 42293.323609226594 2011 USED 17618.325536062377 2021 USED 48976.94940202392 1998 USED 24038.666666666668 2017 USED 35918.37127976191 1959 USED 1500000.0 1984 USED 148880.0 2008 USED 17265.117283950618 1999 USED 23023.103448275862 2020 NEW null 2023 NEW 77896.7590759076 2010 USED 16829.785398230088 1992 USED 17688.0 1994 USED 45051.333333333336 2018 USED 38294.09033877039 2023 DEMO 65045.868131868134 1975 USED 39990.0 2006 USED 13834.456621004567 2014 USED 23784.113402061856 2022 USED 61828.68378378378 2009 USED 15134.588709677419

Databricks visualization. Run in Databricks to view.

### Média de Valores em relação a Marca

In [0]:

brand_price = df.groupBy("Brand").agg(avg("Price").alias("AveragePrice")).orderBy("AveragePrice")
display(brand_price)

Brand AveragePrice Daewoo 900.0 Smart 5985.0 Geely 6450.0 Saab 6699.5 Proton 7990.0 Opel 12172.25 Great 13059.6875 Tata 16990.0 Fiat 19933.34375 Holden 21117.456221198157 Citroen 21875.333333333332 Suzuki 23644.8127090301 Alfa 24295.85714285714 Honda 24642.740331491714 Peugeot 25354.22033898305 Dodge 25870.23076923077 Hyundai 26214.543973941367 Foton 26244.5 Daihatsu 26423.9 Subaru 26825.673179396093 Nissan 27492.209852216747 Kia 28480.740372670807 Mitsubishi 28572.04646660213 Infiniti 28990.0 MG 29875.658783783783 Datsun 29888.0 Mazda 30224.382176520994 Chery 30475.30769230769 Chrysler 31847.96153846154 Haval 32173.809523809523 Mahindra 33030.0 Renault 33188.68539325843 Rover 33221.333333333336 Ford 33354.51612903226 LDV 36799.1 Volkswagen 37420.42728297632 Abarth 37490.0 Skoda 38111.7027027027 Mini 38310.78313253012 Toyota 38825.34699057288 Ssangyong 39676.43859649123 GWM 40308.98469387755 Jeep 42758.025 BYD 44950.0 Volvo 45098.352459016394 Isuzu 51329.34703196347 BMW 51608.955882352944 Audi 51870.44880174292 FPV 52367.4 Lexus 57375.67955801105 Mercedes-Benz 57454.2576489533 Jaguar 61018.9 Packard 64990.0 Cupra 65716.66666666667 Land 73846.41101694915 HSV 76732.81818181818 Polestar 79900.0 Tesla 86317.8 Genesis 98190.85714285714 Caterham 103941.0 Ineos 109275.0 Ram 111425.05882352941 Hino 122968.76923076923 Maserati 128872.9375 Porsche 137256.44329896907 Chevrolet 150111.0 Iveco 156622.7027027027 Lotus 163990.0 Aston 284275.8 Bentley 289942.1666666667 Rolls-Royce 329990.0 International 341687.5 McLaren 443588.5 Ferrari 507441.0 Lamborghini 542440.0

Databricks visualization. Run in Databricks to view.

### Média de Valores em relação a Marca e o ano do Veículo

In [0]:
brand_year_price = df.groupBy(["Brand", "Year"]).agg(avg("Price").alias("AveragePrice")).orderBy("AveragePrice")
display(brand_year_price)

Brand Year AveragePrice Nissan 1993 null Alfa 2006 88.0 Daewoo 1998 900.0 Volkswagen 2003 2050.0 Ford 1999 2500.0 Toyota 1995 2995.0 Hyundai 2003 2999.0 Honda 2001 3499.0 Audi 2001 3990.0 Skoda 2008 3999.0 Subaru 2002 4995.0 Mercedes-Benz 1999 4999.0 Honda 1990 4999.0 Subaru 2003 4999.0 Saab 2008 5400.0 Mazda 2001 5429.666666666667 Holden 1992 5488.0 Hyundai 2000 5490.0 Hyundai 2001 5494.0 Ford 1996 5747.0 Audi 2003 5888.0 Smart 2007 5985.0 Chery 2013 5990.0 Suzuki 2002 5994.5 Kia 2004 5999.0 Volvo 2003 5999.0 Honda 2003 6249.5 Hyundai 2004 6392.833333333333 Geely 2012 6450.0 Holden 1996 6499.0 Kia 2008 6562.454545454545 Mazda 2000 6632.25 Hyundai 2006 6718.5 Peugeot 2007 6749.5 Kia 2005 6796.333333333333 Mazda 2003 6916.0 Mazda 2004 6931.125 BMW 1997 6988.0 Renault 2003 6990.0 Honda 2002 6990.0 Mitsubishi 1998 6990.0 Audi 2004 6995.0 Volkswagen 2001 6999.0 Peugeot 2006 6999.0 Hyundai 2008 7059.333333333333 Subaru 2004 7292.666666666667 Mercedes-Benz 2002 7294.666666666667 Honda 2005 7364.111111111111 Honda 1998 7387.0 Chrysler 2008 7460.75 Suzuki 2006 7656.833333333333 GWM 2009 7750.0 Mazda 1999 7788.0 Hyundai 2005 7796.555555555556 Lexus 1998 7888.0 Peugeot 2010 7888.0 Suzuki 2005 7907.666666666667 Kia 2007 7974.8 Peugeot 2005 7990.0 Proton 2009 7990.0 Hyundai 2002 7990.0 Lexus 2003 7990.0 Holden 1999 7990.0 Chery 2011 7999.0 Kia 2006 7999.0 Volkswagen 2004 7999.0 Kia 2001 7999.0 Saab 2007 7999.0 Honda 2004 8328.0 Mazda 2005 8362.75 Volkswagen 2005 8425.666666666666 Ford 2000 8490.0 Chrysler 2002 8492.0 Audi 2000 8494.5 Peugeot 2009 8744.5 Honda 2006 8866.888888888889 Mitsubishi 2000 8900.0 Mitsubishi 2001 8926.666666666666 Suzuki 2007 8990.0 GWM 2012 8990.0 Land 2001 8995.0 Ssangyong 2011 8999.0 Volvo 2008 8999.0 Toyota 2001 9216.875 BMW 2004 9295.4 Ford 2007 9382.941176470587 BMW 2003 9494.5 Citroen 2011 9494.5 Jeep 2005 9499.0 Holden 2006 9755.55 Ssangyong 2009 9790.0 Hyundai 2007 9792.6 Suzuki 2009 9822.0 Honda 2007 9837.058823529413 Great 2014 9980.0 Volvo 2004 9990.0 Daihatsu 1990 9990.0 Peugeot 2008 9990.0 Volkswagen 2006 9993.0 Great 2012 9994.5 Mini 2004 9995.0 Fiat 2012 9995.0 Alfa 2013 9997.0 Chrysler 2009 9999.0 Mercedes-Benz 2001 9999.0 Renault 2008 9999.0 BMW 2005 9999.0 Land 2004 9999.0 Ford 2005 10010.111111111111 Ford 2004 10036.90909090909 Volvo 2009 10146.833333333334 Volkswagen 2007 10244.818181818182 Dodge 2010 10250.0 Suzuki 2012 10254.5 Lexus 2007 10299.666666666666 Opel 2013 10349.5 Holden 1998 10494.5 Mazda 2006 10549.388888888889 Great 2013 10659.0 Mercedes-Benz 2000 10659.666666666666 Subaru 2006 10695.545454545454 Toyota 2002 10725.05 Volkswagen 2009 10824.9 Jaguar 2004 10888.0 Kia 2009 10889.555555555555 Alfa 2014 10895.333333333334 Skoda 2010 10906.666666666666 Ssangyong 2013 10910.0 Hyundai 2009 10912.772727272728 Citroen 2012 10990.0 Lexus 2006 10990.0 Jeep 2006 10994.5 Dodge 2012 10999.0 Suzuki 2008 11012.285714285714 Holden 2007 11018.344827586207 Kia 2010 11060.055555555555 Toyota 2000 11173.733333333334 Mazda 2007 11233.2 Mazda 2009 11247.12 Holden 2005 11308.884615384615 Great 2011 11326.333333333334 Great 2009 11499.0 Ford 2006 11515.666666666666 Suzuki 2010 11531.4 Mazda 2010 11554.454545454546 Jeep 2008 11576.333333333334 Skoda 2012 11633.0 Mazda 2008 11672.875 Suzuki 2011 11745.181818181818 Hyundai 2010 11748.375 Volvo 2010 11902.0 Honda 2008 11933.0 Dodge 2014 11999.0 Honda 2010 12109.25 Fiat 2014 12117.714285714286 Audi 2007 12253.57142857143 Holden 2008 12313.382352941177 Volvo 2011 12326.333333333334 Volkswagen 2008 12342.1 Kia 2011 12366.583333333334 Honda 2009 12405.75 Mercedes-Benz 2008 12497.2 Mitsubishi 2009 12720.833333333334 Fiat 2013 12737.25 Ford 2010 12879.90909090909 Alfa 2008 12890.0 Lexus 2005 12899.25 Ford 1990 12900.0 Hyundai 2011 12966.027777777777 Volvo 2007 12990.0 Alfa 2012 12990.0 Mini 2006 12995.0 Foton 2013 12999.0 Dodge 2009 12999.0 Audi 2009 13161.666666666666 Holden 2009 13208.820512820514 Kia 2012 13222.227272727272 Nissan 2001 13263.8 Audi 2008 13328.0 N

Databricks visualization. Run in Databricks to view.

###Distribuição de Preços por Tipo de Veículo

In [0]:
body_type = df.select('Price', 'BodyType')
display(body_type)

Price BodyType 51990 SUV 19990 Hatchback 108988 Coupe 32990 Coupe 34990 SUV 9990 Commercial 62280 SUV 2995 Hatchback 24888 Coupe 17900 Hatchback 42500 Commercial 41999 Commercial 11999 null 38999 null 27995 Commercial 14999 Hatchback 24985 SUV 13999 Wagon 13999 Hatchback 12400 Hatchback 13999 SUV 11999 Hatchback 83887 Ute / Tray 19900 Hatchback 17990 SUV 14995 Hatchback 8499 Sedan 21999 null 12990 Sedan 16999 SUV 21950 SUV 24880 Hatchback 35887 Wagon 23888 SUV 16999 Hatchback 24490 SUV 44878 Hatchback 7949 Sedan 13999 Wagon 8800 Hatchback 32900 Commercial 13990 SUV 9999 Commercial 14999 Sedan 22750 Ute / Tray 21950 Coupe 19999 Hatchback 19900 Coupe 37990 SUV 12990 Hatchback 16999 Sedan 36990 Hatchback 23880 SUV 10990 Sedan 44900 People Mover 15880 Hatchback 16995 Sedan 19880 SUV 43999 SUV 18888 SUV 24995 Convertible 9998 SUV 9990 Sedan 27380 Coupe 24999 Hatchback 17999 SUV 12990 SUV 13990 SUV 28990 Convertible 36800 SUV 13999 Sedan 56887 SUV 19888 Wagon 8995 Hatchback 31900 SUV 14995 Sedan 22990 SUV 31990 Hatchback 12999 Hatchback 25999 Ute / Tray 13990 Hatchback 30990 Ute / Tray 8499 Sedan 10995 Hatchback 24888 Wagon 11669 SUV 24950 SUV 16990 Sedan 19995 Wagon 13995 Wagon 17995 Sedan 22990 Hatchback 16999 Hatchback 79988 SUV 12800 SUV 26880 Coupe 16990 Hatchback 16999 null 30900 Commercial 34888 null 28999 SUV 13880 Hatchback 17950 Sedan 33888 SUV 39990 SUV 23950 SUV 41950 SUV 21999 Hatchback 27990 SUV 8950 Sedan 37880 SUV 7950 Hatchback 24990 SUV 14999 SUV 22999 Sedan 7999 Coupe 10999 Wagon 19999 Sedan 30999 Commercial 15990 Sedan 32888 SUV 31900 Commercial 22999 Wagon 10995 Hatchback 29990 SUV 13950 Hatchback 36999 Ute / Tray 9990 Wagon 24990 Coupe 13990 Hatchback 16990 Hatchback 10995 Sedan 12990 Hatchback 18990 Hatchback 23999 Hatchback 14995 Hatchback 18995 Ute / Tray 14990 Hatchback 29950 Hatchback 22999 Wagon 14990 Hatchback 7888 Sedan 27990 Wagon 19800 Ute / Tray 67988 Sedan 21880 Wagon 41888 SUV 17900 Commercial 18900 Commercial 29990 SUV 7920 Hatchback 14999 Hatchback 38950 SUV 16999 Hatchback 12990 Hatchback 29990 SUV 29990 SUV 214880 Coupe 8950 SUV 26280 Hatchback 21290 Ute / Tray 22900 Commercial 14995 SUV 21290 Ute / Tray 16388 Hatchback 26990 SUV 32000 SUV 67988 Sedan 7600 Hatchback 17990 Hatchback 19950 Sedan 9990 Hatchback 129988 Coupe 7999 Hatchback 9995 Commercial 19900 Commercial 16990 Hatchback 17888 SUV 18995 Ute / Tray 16857 SUV 22990 SUV 13950 Ute / Tray 12990 SUV 22990 Hatchback 59990 Hatchback 21880 Ute / Tray 10990 SUV 39990 Sedan 39990 Hatchback 21990 Ute / Tray 18990 Hatchback 39990 SUV 21990 Ute / Tray 31990 SUV 26990 SUV 32900 Commercial 28999 Ute / Tray 22500 Hatchback 17990 Commercial 27800 SUV 29990 Hatchback 10990 Hatchback 34800 SUV 28984 SUV 32990 Sedan 19999 Sedan 29990 SUV 16990 SUV 10800 Hatchback 39880 SUV 14995 Sedan 27990 Sedan 22990 Hatchback 14995 Hatchback 39280 SUV 10990 Hatchback 47990 Sedan 23950 SUV 26990 Hatchback 7990 Hatchback 28999 Hatchback 17900 Sedan 16990 Hatchback 26990 Hatchback 34913 Ute / Tray 19990 Hatchback 55888 Sedan 24950 SUV 12800 Hatchback 41280 Hatchback 13990 Hatchback 33898 SUV 8913 SUV 14888 Hatchback 15995 Sedan 48999 Ute / Tray 12990 Ute / Tray 23990 Hatchback 24888 Sedan 13999 Hatchback 27950 Hatchback 13990 Hatchback 19999 SUV 22950 Commercial 14990 Hatchback 69800 SUV 20995 SUV 14413 Ute / Tray 14776 Sedan 29990 Sedan 7950 Sedan 7949 Sedan 29999 SUV 8880 Sedan 12990 Wagon 9999 Coupe 19888 SUV 5950 Sedan 51990 SUV 16000 Sedan 33990 Ute / Tray 16990 Hatchback 15999 null 36888 SUV 16999 SUV 29800 Sedan 22990 SUV 23913 Ute / Tray 8990 Sedan 29999 Ute / Tray 16420 Hatchback 16990 Hatchback 7880 Sedan 38999 null 21995 Hatchback 5999 Hatchback 18990 Hatchback 27995 SUV 8995 Sedan 7995 Hatchback 30888 SUV 39990 Hatchback 24990 SUV 39990 SUV 54990 SUV 23690 SUV 28990 Ute / Tray 34990 Sedan 79800 Commercial 11490 Hatchback 18995 Hatchback 34995 Commercial 7995 Wagon 49913 Ute / Tray 23400 Hatchback 44990 Hatchback 12995 Sedan 15800 null 23913 SUV 9888 Sedan 1

Databricks visualization. Run in Databricks to view.

In [0]:
engine_capacity = df.groupBy(["EngineCapacity"]).agg(avg("Price").alias("AveragePrice")).orderBy("EngineCapacity")
display(engine_capacity)

EngineCapacity AveragePrice null 40444.26771336554 0.7 5985.0 0.9 12325.0 1.2 22365.425087108015 1.3 30102.23157894737 1.4 23545.35714285714 1.5 29057.943734015345 1.6 22604.614711033275 1.7 17003.333333333332 1.8 20933.3125 1.9 25069.625 2.1 33401.4375 2.2 32157.6511627907 2.3 32981.17840375587 2.4 28187.13017751479 2.5 33917.67778439548 2.6 22194.333333333332 2.7 21381.236842105263 2.8 46942.66218487395 2.9 98353.07692307692 3.1 13888.0 3.2 34424.81798245614 3.3 58717.852459016394 3.4 110255.4 3.5 35877.918699186994 3.6 33550.86522911051 3.7 37409.6 3.8 67653.28301886792 3.9 95470.44444444444 4.1 62246.5 4.2 36348.666666666664 4.3 149969.75 4.4 162102.52 4.5 85938.90728476821 4.6 39888.0 4.7 74624.7 4.8 29283.0 4.9 37747.5 5.1 107496.09090909091 5.2 171056.6 5.3 69990.0 5.4 27064.916666666668 5.5 75814.85714285714 5.6 89930.91666666667 5.7 71567.28846153847 5.9 107494.5 6.1 26999.0 6.2 89978.69117647059 6.3 579888.0 6.4 65787.625 6.5 629940.0 6.6 329990.0 6.7 151173.2 6.8 254526.66666666666 7.3 79900.0 7.7 167108.66666666666 7.8 171502.4 8.9 200346.0 9.8 266942.5

Databricks visualization. Run in Databricks to view.

In [0]:
seats_capacity = df.groupBy(["Seats"]).agg(avg("Price").alias("AveragePrice")).orderBy("Seats")
display(seats_capacity)

Seats AveragePrice null 39623.849127182046 11 Seats 36316.0 12 Seats 72672.5 14 Seats 35320.5 15 Seats 91537.0 2 Seats 54392.22428330523 22 Seats 149084.0 3 Seats 46874.64634146341 4 Seats 54010.79821958457 5 Seats 34040.9764288879 6 Seats 44060.89655172414 7 Seats 41328.44879686626 8 Seats 38739.32352941176 9 Seats 34653.333333333336

## Preferências de Consumo 

### Popularidade de Marca

In [0]:
brand_count = df.groupBy(["Brand"]).count().orderBy("count")
display(brand_count)

Brand count Polestar 1 Rolls-Royce 1 Tata 1 Proton 1 Geely 1 Daewoo 1 Datsun 1 Smart 1 Packard 1 International 2 Caterham 2 Saab 2 Abarth 2 Lamborghini 2 Infiniti 3 Rover 3 BYD 3 Lotus 3 Ineos 4 Foton 4 Opel 4 FPV 5 Aston 5 McLaren 8 Ferrari 8 Cupra 9 Daihatsu 10 Mahindra 12 Bentley 12 Chevrolet 13 Chery 13 Dodge 13 Genesis 14 Alfa 14 Tesla 15 Citroen 15 Great 16 Maserati 16 Haval 21 Hino 26 Chrysler 26 Fiat 32 Ram 34 Iveco 37 HSV 44 Jaguar 51 Ssangyong 58 Peugeot 59 Mini 83 Porsche 97 Skoda 111 Volvo 123 LDV 123 Renault 178 Lexus 181 GWM 201 Isuzu 219 Land 236 MG 299 Suzuki 304 Jeep 320 Honda 362 Audi 459 BMW 476 Subaru 564 Mercedes-Benz 621 Kia 807 Volkswagen 888 Nissan 1017 Mitsubishi 1037 Ford 1054 Holden 1085 Mazda 1171 Hyundai 1235 Toyota 2760

Databricks visualization. Run in Databricks to view.